In [2]:
import torch


In [3]:
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline 
import torchvision
import torchvision.transforms.v2 as T
from torch.utils.data import DataLoader , TensorDataset
import torch.nn as nn
import torchmetrics
import torch.nn.functional as F

In [4]:
import optuna

In [5]:
toTensor = T.Compose([T.ToImage() , T.ToDtype(torch.float32 , scale=True)])

train_and_valid_data = torchvision.datasets.FashionMNIST(
    root="datasets" , train=True , download=True , transform=toTensor
)

test_data = torchvision.datasets.FashionMNIST(
    root="datasets" , train=False , download=True , transform=toTensor
)

torch.manual_seed(42)
train_data , valid_data = torch.utils.data.random_split(
    train_and_valid_data , [55_000 , 5_000]
)

In [6]:
train_loader = DataLoader(train_data , shuffle=True , batch_size = 1024 , pin_memory=True , num_workers=4 , prefetch_factor=3)
valid_loader = DataLoader(valid_data , shuffle=True , batch_size = 1024 , pin_memory=True , num_workers=4 , prefetch_factor=3)
test_loader = DataLoader(test_data , shuffle=True , batch_size = 1024 , pin_memory=True , num_workers=4 , prefetch_factor=3)




In [7]:
x_sample , y_sample = train_data[0]

In [8]:
y_sample

9

In [9]:
x_sample.shape

torch.Size([1, 28, 28])

In [10]:
x_sample.dtype

torch.float32

In [11]:
train_and_valid_data.classes[y_sample]

'Ankle boot'

In [12]:
for i in range(1 , 10):
    print(train_and_valid_data.classes[i] , end=" ")

Trouser Pullover Dress Coat Sandal Shirt Sneaker Bag Ankle boot 

In [13]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

print(device)

cuda


In [14]:
n_epoch = 20

In [17]:
def eval(model , metric , val_loader):
    model.eval()
    metric.reset()
    
    with torch.no_grad():
        for x_batch , y_batch in val_loader:
            x_batch , y_batch = x_batch.to(device) , y_batch.to(device)
            
            y_pred = model(x_batch)
            
            metric.update(y_pred , y_batch)
            
    return metric.compute()





def train_eval(model , train_loader , criterion , optimizer ,
               val_loader , metric , n_epoch ):
    
    history = {"train_loss" : [] , "train_metric(accuracy)" : [] , "val_metric(accuracy)" : []}

    for epoch in range(n_epoch):
        model.train()
        metric.reset()
        total_loss = 0
        for x_batch , y_batch in train_loader:
            #data
            x_batch , y_batch = x_batch.to(device) , y_batch.to(device)
            
            #forward
            
            y_pred  = model(x_batch)
            
            #loss 
            
            loss = criterion(y_pred , y_batch)
            total_loss += loss.item()
            
            #optimizer
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            
            metric.update(y_pred , y_batch)
            
        loss_mean = total_loss/len(train_loader)
        
        history["train_loss"].append(loss_mean)
        history["train_metric(accuracy)"].append(metric.compute().item())
        
        history["val_metric(accuracy)"].append(eval(model , metric , val_loader).item())
        
        print(f"Epoch : {epoch + 1}/{n_epoch}, "
              f"Train Loss : {history['train_loss'][-1]}, "
              f"Train Metric ( Accuracy) : {history['train_metric(accuracy)'][-1]}, "
              f"Val Metric (accuracy) : {history['val_metric(accuracy)'][-1]}")
        
        
    return history
            

In [18]:
class ImageClassifier(nn.Module):
    def __init__(self , n_inputs , n_hidden1 , n_hidden2 , n_classes):
        super().__init__()
        self.mlp = nn.Sequential(
            nn.Flatten(),
            nn.Linear(n_inputs , n_hidden1) , 
            nn.ReLU(),
            nn.Linear(n_hidden1 , n_hidden2),
            nn.ReLU(),
            nn.Linear(n_hidden2 , n_classes)
        )
        
        
    def forward(self , x):
        return self.mlp(x)
    
torch.manual_seed(42)
model = ImageClassifier(n_inputs= 28 * 28 , n_hidden1=  300 , 
                        n_hidden2= 100 , n_classes= 10).to(device)

learning_rate = 0.1

sentropy = nn.CrossEntropyLoss()

optimizer = torch.optim.SGD(model.parameters() , lr=learning_rate , momentum=0 )

accuracy_metric = torchmetrics.Accuracy(task='multiclass' , num_classes=10).to(device)

history = train_eval(model=model , 
           train_loader=train_loader,
           criterion=sentropy,
           optimizer=optimizer,
           val_loader=valid_loader,
           metric=accuracy_metric,
           n_epoch=n_epoch)
    

Epoch : 1/20, Train Loss : 1.816263997996295, Train Metric ( Accuracy) : 0.4902363717556, Val Metric (accuracy) : 0.5925999879837036
Epoch : 2/20, Train Loss : 0.9868314089598479, Train Metric ( Accuracy) : 0.6348000168800354, Val Metric (accuracy) : 0.6439999938011169
Epoch : 3/20, Train Loss : 0.8034907711876763, Train Metric ( Accuracy) : 0.6943272948265076, Val Metric (accuracy) : 0.6754000186920166
Epoch : 4/20, Train Loss : 0.7112136008562865, Train Metric ( Accuracy) : 0.7364181876182556, Val Metric (accuracy) : 0.7544000148773193
Epoch : 5/20, Train Loss : 0.6395985627615893, Train Metric ( Accuracy) : 0.768854558467865, Val Metric (accuracy) : 0.7504000067710876
Epoch : 6/20, Train Loss : 0.6073772366400119, Train Metric ( Accuracy) : 0.7787272930145264, Val Metric (accuracy) : 0.7766000032424927
Epoch : 7/20, Train Loss : 0.568897838945742, Train Metric ( Accuracy) : 0.7965999841690063, Val Metric (accuracy) : 0.7860000133514404
Epoch : 8/20, Train Loss : 0.5506595157914691, 

In [22]:
model.eval()

x_new , y_new = next(iter(valid_loader))

print(len(valid_loader))
print(x_new.shape)
x_new = x_new[:3].to(device)
print(x_new.shape)

5
torch.Size([1024, 1, 28, 28])
torch.Size([3, 1, 28, 28])


In [23]:
with torch.no_grad():
    y_pred_logits = model(x_new)
    
    
    
print(y_pred_logits)

y_pred = y_pred_logits.argmax(dim=1)

print(y_pred)

tensor([[-2.1043, -3.1172, -3.6843, -1.7786, -4.7050,  4.6494, -3.5991,  8.3780,
          1.7174,  6.9137],
        [ 1.8747, -4.7915,  2.6901, -1.1148,  1.6494,  0.1401,  2.4506, -2.8027,
          8.4876, -5.0992],
        [ 3.7941, -0.5037,  0.6050,  1.5818, -0.8497, -1.1400,  3.3536, -3.1606,
         -0.6429, -2.0111]], device='cuda:0')
tensor([7, 8, 0], device='cuda:0')


In [24]:
y_proba = F.softmax(y_pred_logits , dim=1)
y_proba.round(decimals = 3)

tensor([[0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0190, 0.0000, 0.7960, 0.0010,
         0.1840],
        [0.0010, 0.0000, 0.0030, 0.0000, 0.0010, 0.0000, 0.0020, 0.0000, 0.9920,
         0.0000],
        [0.5430, 0.0070, 0.0220, 0.0590, 0.0050, 0.0040, 0.3500, 0.0010, 0.0060,
         0.0020]], device='cuda:0')

In [25]:
# getting the top four logits and proba

y_top4_logits , y_top4_indices = torch.topk(y_pred_logits , k=4 , dim=1)
y_top4_proba = F.softmax(y_top4_logits , dim=1)
y_top4_proba.round(decimals = 3)

tensor([[0.7960, 0.1840, 0.0190, 0.0010],
        [0.9930, 0.0030, 0.0020, 0.0010],
        [0.5570, 0.3590, 0.0610, 0.0230]], device='cuda:0')

In [26]:
y_top4_indices

tensor([[7, 9, 5, 8],
        [8, 2, 6, 0],
        [0, 6, 3, 2]], device='cuda:0')

In [27]:
#fine tuning the model using optuna

In [28]:
def objective(trial):
    learning_rate = trial.suggest_float("learning_rate" , 1e-5 , 1e-1 , log=True)
    n_hidden = trial.suggest_int("n_hidden" , 20 , 300)
    model = ImageClassifier(n_inputs= 1 * 28 * 28 , n_hidden1= n_hidden , n_hidden2=n_hidden,
                            n_classes=10 ).to(device)
    
    optimizer = torch.optim.SGD(model.parameters() , momentum=0 , lr = learning_rate)
    
    
    xentropy = nn.CrossEntropyLoss()
    
    accuracy_metric = torchmetrics.Accuracy(task = "multiclass" , num_classes=10).to(device)
    
    best_val_score = 0.0
    
    for epoch in range(n_epoch):
        history = train_eval(model , train_loader , xentropy , optimizer , 
                             valid_loader , accuracy_metric , n_epoch)
        
        val_score = max(history['val_metric(accuracy)'])
        
        if val_score > best_val_score:
            best_val_score = val_score
            
        trial.report(val_score , epoch)
        
        if trial.should_prune():
            raise optuna.TrialPruned()
        
    
    return best_val_score
        
        
    
        
    

In [ ]:
# torch.manual_seed(42)
sampler = optuna.samplers.TPESampler(seed = 42)
study = optuna.create_study(direction="maximize" , sampler=sampler)
# study.optimize(objective , n_trials=5)



# 73 min 


[I 2026-01-28 05:59:54,647] A new study created in memory with name: no-name-4c85b624-a34f-4fec-870f-c4bd564e8e10


Epoch : 1/20, Train Loss : 2.307674041500798, Train Metric ( Accuracy) : 0.09545454382896423, Val Metric (accuracy) : 0.09399999678134918
Epoch : 2/20, Train Loss : 2.3056274784935846, Train Metric ( Accuracy) : 0.10129091143608093, Val Metric (accuracy) : 0.10379999876022339
Epoch : 3/20, Train Loss : 2.3035900725258722, Train Metric ( Accuracy) : 0.10816363990306854, Val Metric (accuracy) : 0.11060000211000443
Epoch : 4/20, Train Loss : 2.301559465902823, Train Metric ( Accuracy) : 0.11427272856235504, Val Metric (accuracy) : 0.11559999734163284
Epoch : 5/20, Train Loss : 2.2995285193125405, Train Metric ( Accuracy) : 0.12067272514104843, Val Metric (accuracy) : 0.12099999934434891
Epoch : 6/20, Train Loss : 2.2974877622392444, Train Metric ( Accuracy) : 0.12592726945877075, Val Metric (accuracy) : 0.12540000677108765
Epoch : 7/20, Train Loss : 2.2954777346716986, Train Metric ( Accuracy) : 0.1300181746482849, Val Metric (accuracy) : 0.13099999725818634
Epoch : 8/20, Train Loss : 2.2

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x78cdaf733380>
Traceback (most recent call last):
  File "/home/ateeksh/mlrepos/mllibraries/lib/python3.12/site-packages/torch/utils/data/dataloader.py", line 1654, in __del__
    self._shutdown_workers()
  File "/home/ateeksh/mlrepos/mllibraries/lib/python3.12/site-packages/torch/utils/data/dataloader.py", line 1637, in _shutdown_workers
    if w.is_alive():
       ^^^^^^^^^^^^
  File "/usr/lib/python3.12/multiprocessing/process.py", line 160, in is_alive
    assert self._parent_pid == os.getpid(), 'can only test a child process'
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
AssertionError: can only test a child process


Epoch : 17/20, Train Loss : 1.3502617390067488, Train Metric ( Accuracy) : 0.6323999762535095, Val Metric (accuracy) : 0.6287999749183655
Epoch : 18/20, Train Loss : 1.3456943145504705, Train Metric ( Accuracy) : 0.6327090859413147, Val Metric (accuracy) : 0.6287999749183655
Epoch : 19/20, Train Loss : 1.3413369015411094, Train Metric ( Accuracy) : 0.6328545212745667, Val Metric (accuracy) : 0.6287999749183655
Epoch : 20/20, Train Loss : 1.3368794211634882, Train Metric ( Accuracy) : 0.6331818103790283, Val Metric (accuracy) : 0.6281999945640564
Epoch : 1/20, Train Loss : 1.3324705980442189, Train Metric ( Accuracy) : 0.6337636113166809, Val Metric (accuracy) : 0.628600001335144
Epoch : 2/20, Train Loss : 1.328129393083078, Train Metric ( Accuracy) : 0.6337817907333374, Val Metric (accuracy) : 0.6287999749183655
Epoch : 3/20, Train Loss : 1.3237363718174122, Train Metric ( Accuracy) : 0.6340181827545166, Val Metric (accuracy) : 0.6290000081062317
Epoch : 4/20, Train Loss : 1.3194311040

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x78cdaf733380>
Traceback (most recent call last):
  File "/home/ateeksh/mlrepos/mllibraries/lib/python3.12/site-packages/torch/utils/data/dataloader.py", line 1654, in __del__
    self._shutdown_workers()
  File "/home/ateeksh/mlrepos/mllibraries/lib/python3.12/site-packages/torch/utils/data/dataloader.py", line 1637, in _shutdown_workers
    if w.is_alive():
       ^^^^^^^^^^^^
  File "/usr/lib/python3.12/multiprocessing/process.py", line 160, in is_alive
    assert self._parent_pid == os.getpid(), 'can only test a child process'
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
AssertionError: can only test a child process


...

Epoch : 17/20, Train Loss : 0.5318186967461197, Train Metric ( Accuracy) : 0.8170182108879089, Val Metric (accuracy) : 0.8090000152587891


Exception ignored in: Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x78cdaf733380><function _MultiProcessingDataLoaderIter.__del__ at 0x78cdaf733380>
Traceback (most recent call last):

  File "/home/ateeksh/mlrepos/mllibraries/lib/python3.12/site-packages/torch/utils/data/dataloader.py", line 1654, in __del__
Traceback (most recent call last):
      File "/home/ateeksh/mlrepos/mllibraries/lib/python3.12/site-packages/torch/utils/data/dataloader.py", line 1654, in __del__
self._shutdown_workers()    
self._shutdown_workers()Exception ignored in:   File "/home/ateeksh/mlrepos/mllibraries/lib/python3.12/site-packages/torch/utils/data/dataloader.py", line 1637, in _shutdown_workers

<function _MultiProcessingDataLoaderIter.__del__ at 0x78cdaf733380>      File "/home/ateeksh/mlrepos/mllibraries/lib/python3.12/site-packages/torch/utils/data/dataloader.py", line 1637, in _shutdown_workers

if w.is_alive():Traceback (most recent call last):
    
  File "/home/atee

Epoch : 18/20, Train Loss : 0.5313705415637405, Train Metric ( Accuracy) : 0.8174545168876648, Val Metric (accuracy) : 0.8086000084877014
Epoch : 19/20, Train Loss : 0.5306659545059558, Train Metric ( Accuracy) : 0.81776362657547, Val Metric (accuracy) : 0.807200014591217
Epoch : 20/20, Train Loss : 0.5297728545135922, Train Metric ( Accuracy) : 0.817727267742157, Val Metric (accuracy) : 0.8094000220298767
Epoch : 1/20, Train Loss : 0.5288325768929941, Train Metric ( Accuracy) : 0.8179818391799927, Val Metric (accuracy) : 0.8098000288009644
Epoch : 2/20, Train Loss : 0.5282385051250458, Train Metric ( Accuracy) : 0.8183454275131226, Val Metric (accuracy) : 0.8090000152587891
Epoch : 3/20, Train Loss : 0.5275543238277789, Train Metric ( Accuracy) : 0.8186545372009277, Val Metric (accuracy) : 0.8109999895095825
Epoch : 4/20, Train Loss : 0.5263680054081811, Train Metric ( Accuracy) : 0.8191999793052673, Val Metric (accuracy) : 0.8100000023841858
Epoch : 5/20, Train Loss : 0.5260661271987

[I 2026-01-28 07:13:31,310] Trial 4 finished with value: 0.8360000252723694 and parameters: {'learning_rate': 0.002537815508265664, 'n_hidden': 218}. Best is trial 1 with value: 0.8651999831199646.


Epoch : 20/20, Train Loss : 0.4513865218118385, Train Metric ( Accuracy) : 0.8427818417549133, Val Metric (accuracy) : 0.8331999778747559


In [ ]:
# study.best_params

# {'learning_rate': 0.008471801418819975, 'n_hidden': 188}

{'learning_rate': 0.008471801418819975, 'n_hidden': 188}

In [ ]:
# study.best_value

# 0.8651999831199646

0.8651999831199646

In [26]:
#wanna pass train and val data loaders directly to the objective functino instead of 
# assuming that they can be accessed via global variables



In [27]:
def objective(trial , train_loader , valid_loader):
    learning_rate = trial.suggest_float("learning_rate" , 1e-5 , 1e-1 , log=True)
    n_hidden = trial.suggest_int("n_hidden" , 20 , 300)
    model = ImageClassifier(n_inputs= 1 * 28 * 28 , n_hidden1= n_hidden , n_hidden2=n_hidden,
                            n_classes=10 ).to(device)
    
    optimizer = torch.optim.SGD(model.parameters() , momentum=0 , lr = learning_rate)
    
    
    xentropy = nn.CrossEntropyLoss()
    
    accuracy_metric = torchmetrics.Accuracy(task = "multiclass" , num_classes=10).to(device)
    
    best_val_score = 0.0
    
    for epoch in range(n_epoch):
        history = train_eval(model , train_loader , xentropy , optimizer , 
                             valid_loader , accuracy_metric , n_epoch)
        
        val_score = max(history['val_metric(accuracy)'])
        
        if val_score > best_val_score:
            best_val_score = val_score
            
        trial.report(val_score , epoch)
        
        if trial.should_prune():
            raise optuna.TrialPruned()
        
    
    return best_val_score
        
        
    
        
    

In [ ]:
# objective_with_data = lambda trial : objective (
#     trial , train_loader=train_loader , valid_loader=valid_loader
# )

In [ ]:
# from functools import partial 

# objective_with_data = partial(objective , train_loader = train_loader , 
#                               valid_loader =  valid_loader)

In [30]:
pruner = optuna.pruners.MedianPruner(n_startup_trials=5 , n_warmup_steps= 0 , 
                                     interval_steps=1)

study = optuna.create_study(direction="maximize" , sampler=sampler , 
                            pruner=pruner)

[I 2026-01-28 13:25:17,017] A new study created in memory with name: no-name-9a504336-d00c-41bc-90ee-416113a187d5


In [31]:
# saving a pytorch model 

In [19]:
torch.save(model , "my_fashion_mnist.pt")

In [20]:
loaded_model = torch.load(
    'my_fashion_mnist.pt' , 
    weights_only=False
)

In [29]:
loaded_model.eval()
y_pred_logits = loaded_model(x_new)

In [30]:
y_pred_logits

tensor([[-2.1043, -3.1172, -3.6843, -1.7786, -4.7050,  4.6494, -3.5991,  8.3780,
          1.7174,  6.9137],
        [ 1.8747, -4.7915,  2.6901, -1.1148,  1.6494,  0.1401,  2.4506, -2.8027,
          8.4876, -5.0992],
        [ 3.7941, -0.5037,  0.6050,  1.5818, -0.8497, -1.1400,  3.3536, -3.1606,
         -0.6429, -2.0111]], device='cuda:0', grad_fn=<AddmmBackward0>)

In [37]:
model_data = {
    'model_state_dict' : model.state_dict(),
    'model_parameters' : {'n_inputs' : 1 * 28 * 28 , 'n_hidden1' : 300 , 'n_hidden2' : 100 , 'n_classes' : 10}             #and so on
}

In [38]:
torch.save(model_data , 'my_fashion_mnist_model_2.pt') 

In [39]:
loaded_data = torch.load('my_fashion_mnist_model_2.pt' , weights_only=True)

In [40]:
loaded_data

{'model_state_dict': OrderedDict([('mlp.1.weight',
               tensor([[ 2.7304e-02,  2.9643e-02, -8.3692e-03,  ..., -1.4307e-02,
                         9.2343e-03,  1.3434e-02],
                       [-1.8809e-02, -3.5415e-02,  1.8657e-02,  ..., -1.0152e-02,
                         4.0481e-06,  1.1550e-02],
                       [-7.8470e-04,  1.6534e-03,  4.5181e-03,  ..., -1.2954e-02,
                        -1.8868e-02,  5.8563e-03],
                       ...,
                       [-2.8290e-02,  1.5996e-02, -3.3101e-02,  ..., -2.2010e-02,
                        -2.8597e-02,  2.4751e-03],
                       [ 1.4948e-02, -2.2230e-02,  1.5816e-02,  ...,  1.2715e-04,
                         8.9895e-04,  9.9869e-04],
                       [ 6.0325e-03, -6.2269e-03, -1.1216e-02,  ...,  1.5307e-02,
                         1.0979e-02, -5.3448e-03]], device='cuda:0')),
              ('mlp.1.bias',
               tensor([ 3.1251e-02,  7.7437e-03,  2.4766e-02,  5.1361e-02,

In [41]:
newModel = ImageClassifier(**loaded_data['model_parameters'])
newModel.load_state_dict(loaded_data['model_state_dict'])
newModel.eval()






ImageClassifier(
  (mlp): Sequential(
    (0): Flatten(start_dim=1, end_dim=-1)
    (1): Linear(in_features=784, out_features=300, bias=True)
    (2): ReLU()
    (3): Linear(in_features=300, out_features=100, bias=True)
    (4): ReLU()
    (5): Linear(in_features=100, out_features=10, bias=True)
  )
)